
# Integrating Databricks with AWS Kinesis

In this notebook, we will use pyspark to stream data from Kinesis to Databricks. Firstly, we will read streaming data from Kinesis in Databricks and then perform transformations on the 3 Kinesis streams. Once this is complete, we will then write the transformed streams to Delta tables in Kinesis. 

## Reading streaming data from Kinesis

In [0]:
# Checking to see if the credential files is in the directory:
dbutils.fs.ls("/FileStore/tables")

Out[1]: [FileInfo(path='dbfs:/FileStore/tables/authentication_credentials.csv', name='authentication_credentials.csv', size=202, modificationTime=1687110999000)]

In [0]:
# The following libraries are required:
# pyspark functions and types:
from pyspark.sql.functions import *
from pyspark.sql.types import *
# URL processing:
import urllib

In [0]:
# To read the authentication_credentials.csv files:
# Specifying the file type to be csv:
file_type = "csv"
# Indicating the file's first row is the header:
first_row_is_header = 'true'
# Indicating the delimiter is a comma:
delimiter = ","
# Reading the csv file to a Spark dataframe:
aws_keys_df = spark.read.format(file_type)\
    .option("header", first_row_is_header)\
    .option("sep", delimiter)\
    .load("/FileStore/tables/authentication_credentials.csv")

In [0]:
# Extracting the AWS access key and secret access key from the Spark dataframe created above:
ACCESS_KEY = aws_keys_df.where(col("User name")=='databricks-user').select('Access key ID').collect()[0]['Access key ID']
SECRET_KEY = aws_keys_df.where(col('User name')=='databricks-user').select('Secret access key').collect()[0]['Secret access key']
# Encoding the secret key for security purposes:
ENCODED_SECRET_KEY = urllib.parse.quote(string=SECRET_KEY, safe="")

In [0]:
# Once data is continuously being sent to the 3 kinesis streams we can use the access key and secret key to read the streaming date into spark dataframes

In [0]:
# For the Pinterest posts data:
pin_0e1f6d6285c1_df = spark \
.readStream \
.format('kinesis') \
.option('StreamName','streaming-0e1f6d6285c1-pin') \
.option('initialPosition','earliest') \
.option('region','us-east-1') \
.option('awsAccessKey', ACCESS_KEY) \
.option('awsSecretKey', SECRET_KEY) \
.load()

# Displaying the dataframe, this is the data arriving from Kinesis in the default schema of Kinesis: partitionKey, data, stream, shardId, sequenceNnumber, approximateArrivalTimestamp
display(pin_0e1f6d6285c1_df)

partitionKey data stream shardId sequenceNumber approximateArrivalTimestamp pin_partition eyJpbmRleCI6MTA2OTcsInVuaXF1ZV9pZCI6IjI3MDJlZDQ0LTkxZjctNDQ1My05MjcwLTQ3MmI1NmYwYWFhNiIsInRpdGxlIjoiQ2xhc3NpYyBGb3JkIEJyb25jb3MgfCBVbml2ZXJpc3R5IFBhcmsgfCBDb3lvdGUgQnJvbmM= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044738922353066898276738488336434 2023-10-18T14:17:22.931+0000 pin_partition eyJpbmRleCI6MTEyNiwidW5pcXVlX2lkIjoiM2I3N2Y2YmEtMWU0Zi00YmNkLWIwOWItNDM3OGZmZDEzNzM5IiwidGl0bGUiOiIxMyBXYXlzIFRvIEdldCBSaWQgb2YgRGFyayBDaXJjbGVzIFVuZGVyIFRoZSBFeWVzIiwiZGU= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044739831465283248478084025810994 2023-10-18T14:17:25.302+0000 pin_partition eyJpbmRleCI6NTM3MiwidW5pcXVlX2lkIjoiMWI4Y2ZmZmItYTg4YS00NTc3LWIwM2ItMDU2NjAxYzJmODA2IiwidGl0bGUiOiJGaW5hbmNpYWwgUGVhY2UiLCJkZXNjcmlwdGlvbiI6IjkgUGVyc29uYWwgRmluYW5jZSBNaWw= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044740694638318453323452204974130 2023-10-18T14:17:27.682+0000 pin_partition eyJpbmRleCI6MjQ2MywidW5pcXVlX2lkIjoiMGNlYTVjMTItZTZkNy00MjhmLWEzZWEtOThlMDRmZTc5NWU1IiwidGl0bGUiOiJBIENvenkgQ291Y2ggZm9yIG91ciBCaWcgRmFtaWx5ISAtIENvdHRvbiBTdGVtIiwiZGVzY3I= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044741746403781518050971638300722 2023-10-18T14:17:30.122+0000 pin_partition eyJpbmRleCI6NDkxMywidW5pcXVlX2lkIjoiNGQyZDc5YzYtOWNhOC00NmM5LWEzOGUtOTMxYzVkOTY3ODA0IiwidGl0bGUiOiJIb3cgdG8gV29yayBGcm9tIEhvbWUgYXMgYW4gRXZlbnQgUGxhbm5lciIsImRlc2NyaXB0aW8= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044742677276662621315642320486450 2023-10-18T14:17:32.448+0000 pin_partition eyJpbmRleCI6ODk5NSwidW5pcXVlX2lkIjoiNDg1Y2VkYWMtMWIxNy00NDE0LWJmNjktNDMyMmU0MjlkZjU3IiwidGl0bGUiOiIyMCBDdXRlIEJlaGluZCB0aGUgRWFyIFRhdHRvb3MgZm9yIFdvbWVuIiwiZGVzY3JpcHRpb24= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044743350648344146664161351303218 2023-10-18T14:17:33.885+0000 pin_partition eyJpbmRleCI6OTk0OSwidW5pcXVlX2lkIjoiZTM0NzEyZmQtMWZiMi00YzJlLWEwOTMtMmZkYTNhNmE1OTE3IiwidGl0bGUiOiI4IEZhaXJ5IFRhbGUgVG93bnMgSW4gR2VybWFueSBZb3UgSGF2ZSBUbyBWaXNpdCAtIFRoZUY= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044743910380998628237537959739442 2023-10-18T14:17:35.273+0000 pin_partition eyJpbmRleCI6NjM2NSwidW5pcXVlX2lkIjoiNTZhOGVhOTQtZDAwMy00NzAzLTg1MDctNDhhMjU3OGU4Y2VhIiwidGl0bGUiOiJNYXN0ZXIgQmVkcm9vbSBXaXRoIEJyaWdodCBTcHJpbmcgRWFzdGVybiBSZWRidWQgQnJhbmM= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044744820702140798053443952443442 2023-10-18T14:17:37.636+0000 pin_partition eyJpbmRleCI6OTgxNSwidW5pcXVlX2lkIjoiNzA5YWViNWYtZGYzZi00ZmI0LWI1ZGEtN2Q1NmE0NzA3OGM3IiwidGl0bGUiOiJBIEV1cm9wZSBJdGluZXJhcnkgZm9yIDIgbW9udGhzIGluIEV1cm9wZTogWW91ciBwZXJmZWM= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044745814439164521278831719350322 2023-10-18T14:17:40.033+0000 pin_partition eyJpbmRleCI6NzA5MCwidW5pcXVlX2lkIjoiZjkzZTBiMjgtZTRlYi00MThkLWJjYzItYzQ3OTgzZjQwMGY4IiwidGl0bGUiOiJGYXNoaW9uIENhdXN1YWwgR2VudGxlbWFuIE91dGVyd2VhciBDb2F0IiwiZGVzY3JpcHRpb24= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044746786415523491440825622069298 2023-10-18T14:17:42.502+0000 pin_partition eyJpbmRleCI6NDM1MywidW5pcXVlX2lkIjoiMzNiOTBiNmYtMmEzOS00OWRlLWFjMjgtMWZhMzcwNWY0ZjNmIiwidGl0bGUiOiIxMTUgQWgtTWF6aW5nIEV2ZW50IENvbXBhbnkgTmFtZSBJZGVhcyIsImRlc2NyaXB0aW9uIjo= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970709831841044747317133958302263239476510770 2023-10-18T14:17:43.824+0000 pin_partition eyJpbmRleCI6MzEwOCwidW5pcXVlX2lkIjoiZGQ4MjI2MTctNmIzZS00ZDZlLTk4YWYtMjcyMDhkMmQwYTYzIiwidGl0bGUiOiI2IEVhc3kgV2F5cyBUbyBEcmVzcyBVcCBBIFRpbiBDYW4iLCJkZXNjcmlwdGlvbiI6IkEgQ2g= (truncated) streaming-0e1f6d6285c1-pin shardId-000000000003 49645424600970

In [0]:
# To see the data contained in the pinterest posts stream, we need to deserialise the data column of the dataframe above:
pin_0e1f6d6285c1_df = pin_0e1f6d6285c1_df.selectExpr("CAST(data as STRING)")

# Displaying the dataframe:
display(pin_0e1f6d6285c1_df)

data {"index":3069,"unique_id":"d0af510a-d6e3-4f5a-aff1-941aed7fed0d","title":"World Market Inspired Yarn Cone Trees - Hello Central Avenue","description":"These little World Market inspired yarn cone trees are super EASY to make, which comes in handy since there’s only a week left until Christmas! They are perfect to add to your c… ","poster_name":"Hello Central Avenue-Rebecca | Home Decor, DIY, & Organization","follower_count":"6k","tag_list":"Christmas Tree Crafts,Christmas Projects,Christmas Home,Christmas Holidays,Christmas Decorations,Christmas Ornaments,Outdoor Christmas,Christmas Angels,Happy Holidays","is_image_or_video":"image","image_src":"https://i.pinimg.com/originals/4b/7c/89/4b7c890b13ddac3c4e3fe9c2cc7e94b3.jpg","downloaded":1,"save_location":"Local save in /data/diy-and-crafts","category":"diy-and-crafts"} {"index":780,"unique_id":"88ccaa72-c810-4847-a489-61dd26c486fd","title":"Artist Illustrates How Doing Anything Is Much Better When There Are Animals Around (29 Pics)","description":"Chilling with animals is the best. There's nothing better than vibing with your furry friends; you get the best of both worlds. You can feel like you have company without the un… ","poster_name":"Bored Panda","follower_count":"2M","tag_list":"Cartoon Girl Images,Cartoon Art Styles,Girl Cartoon,Cute Cartoon Girl Drawing,Image Princesse Disney,Arte Sketchbook,Digital Art Girl,Cute Drawings,Drawing Pics","is_image_or_video":"image","image_src":"https://i.pinimg.com/originals/62/22/03/6222032afb7a9c42971e5b644bd9781e.jpg","downloaded":1,"save_location":"Local save in /data/art","category":"art"} {"index":7598,"unique_id":"cfb949d8-2d9b-4170-8d93-04462917d489","title":"She Was A Forgiver. Her Heart Was So Large. She Didn't Know How To Give Up On People","description":"Relationship Rules is a modern-age lifestyle/love blog that discusses everything from breakups to being amazing parents.","poster_name":"Renee Knick","follower_count":"31","tag_list":"Feeling Broken Quotes,Quotes Deep Feelings,Mood Quotes,Positive Quotes,Life Quotes,Broken Promises Quotes,Broken Trust Quotes,Words Hurt Quotes,Qoutes","is_image_or_video":"image","image_src":"https://i.pinimg.com/originals/52/36/0e/52360e5a45b1f6374733183fd40e7f87.png","downloaded":1,"save_location":"Local save in /data/quotes","category":"quotes"} {"index":3145,"unique_id":"1022ba0b-eae7-4eba-9120-1fe44d093a32","title":"How to Colour Chickpeas for Play - Inspire My Play","description":"Learn how to colour chickpeas for sensory play and craft with this easy DIY","poster_name":"Laura- Inspire My Play | Play & Learning For Little Kids","follower_count":"4k","tag_list":"Baby Sensory Play,Sensory Activities Toddlers,Infant Activities,Sensory Bins,Baby Play,Kindergarten Activities,Diy For Kids,Crafts For Kids,Preschool Crafts","is_image_or_video":"image","image_src":"https://i.pinimg.com/originals/35/e0/44/35e0447b94dd9076ed9e51a8d692e489.jpg","downloaded":1,"save_location":"Local save in /data/diy-and-crafts","category":"diy-and-crafts"} {"index":9664,"unique_id":"dff062ed-674c-4833-8118-2f35f8087b3b","title":"51 Beautiful Places to Satisfy Your Wanderlust From Afar","description":"Go globe-trotting (virtually).","poster_name":"House Beautiful","follower_count":"876k","tag_list":"Places Around The World,Travel Around The World,Around The Worlds,Beautiful Places To Travel,Wonderful Places,Amazing Places,Beautiful Things,Dream Vacations,Vacation Spots","is_image_or_video":"image","image_src":"https://i.pinimg.com/originals/af/0d/29/af0d29e8b6343451c7f9464ae9398129.jpg","downloaded":1,"save_location":"Local save in /data/travel","category":"travel"} {"index":8613,"unique_id":"1ae686e8-7f41-433d-bbbd-c3428de9e095","title":"Personalised Viking Rune Initial Talisman Ring By Talisman Kind","description":"A beautiful personalised Viking Rune initial talisman ring.Turn your initial into a gorgeous Viking Rune talisman ring. Here we are using the Elder Futhark Viking language to tu… ","poster_name":"noto

In [0]:
# Converting the above datarame which contains strings for each row into its constituent coloumns and values:
# Converting the above datarame which contains strings for each row into its constituent coloumns and values:
# Defining the schema for the JSON data, the schema specifies the expected data types of each JSON field:
pin_json_schema = StructType([
    StructField("index", IntegerType(), True),
    StructField("unique_id", StringType(), True),
    StructField("title", StringType(), True),
    StructField("description", StringType(), True),
    StructField("poster_name", StringType(), True),
    StructField("follower_count", StringType(), True),
    StructField("tag_list", StringType(), True),  
    StructField("is_image_or_video", StringType(), True),
    StructField("image_src", StringType(), True),
    StructField("downloaded", IntegerType(), True),
    StructField("save_location", StringType(), True),
    StructField("category", StringType(), True),          
])

# Using the from_json function, parse the JSON strings in the "data" column above according to the geo data schema defined above:
pin_parsed_df = pin_0e1f6d6285c1_df.withColumn("pin_parsed_data", from_json(col("data"), pin_json_schema))

# Selecting the values of each column from the parsed geo dataframe:
pin_E_0e1f6d6285c1_df = pin_parsed_df.select(
    col("pin_parsed_data.index").alias("index"),
    col("pin_parsed_data.unique_id").alias("unique_id"),
    col("pin_parsed_data.title").alias("title"),
    col("pin_parsed_data.description").alias("description"),
    col("pin_parsed_data.poster_name").alias("poster_name"),
    col("pin_parsed_data.follower_count").alias("follower_count"),
    col("pin_parsed_data.tag_list").alias("tag_list"),
    col("pin_parsed_data.is_image_or_video").alias("is_image_or_video"),
    col("pin_parsed_data.image_src").alias("image_src"),
    col("pin_parsed_data.downloaded").alias("downloaded"),
    col("pin_parsed_data.save_location").alias("save_location"),
    col("pin_parsed_data.category").alias("category")
)

# Showing the resulting geo dataframe:
display(pin_E_0e1f6d6285c1_df)

index unique_id title description poster_name follower_count tag_list is_image_or_video image_src downloaded save_location category 9613 4d11e997-27a6-4a95-913d-2fa769725ca4 Print - Tranquil Irish Path in County Clare Tranquil Irish Path, County Clare, #Ireland by James A. Truett. James A. Truett - Irish Artist 393 Clare Ireland,Irish Decor,County Clare,Stone Walkway,Home Goods Decor,Irish Art,Irish Blessing,Ireland Travel,Countryside image https://i.pinimg.com/originals/ed/a8/6f/eda86f7abf26e685afab997e776f5314.jpg 1 Local save in /data/travel travel 994 3cf9d8d2-b581-4f90-846e-d47ee16b7e89 60 Second Beauty: Burt's Bees All-Natural Lip Shine and Lip Gloss I have been trying to use more natural products now that I'm expecting, so I was eager to review the Burt's Bees Lip Glosses and Lip Shines that recently landed on my desk. Thes…  The Budget Babe 40k Burts Bees Lip Gloss,Diy Lip Gloss,Burts Bees Makeup,Lipgloss Diy,Burt's Bees Lip Shine,Mac Mehr,Gloss Labial,Natural Lips,Natural Baby image https://i.pinimg.com/originals/00/d8/f3/00d8f34d5b6382f4b03f6df21474b83e.jpg 1 Local save in /data/beauty beauty 5634 5c4df202-5367-4885-9025-e9b395758223 How to Pay No Tax on Your Dividend Income Did you have to pay tax on your dividend income? Here is how to keep that money instead of sending it to Uncle Sam. Pay no tax on dividend income. Retire by 40 5k Investing In Stocks,Investing Money,Saving Money,Stock Investing,Money Savers,Saving Tips,Wealth Management,Money Management,Tax Help image https://i.pinimg.com/originals/3f/a3/90/3fa39017ff6188d929cc7982ad369427.jpg 1 Local save in /data/finance finance 6424 547f52ea-9ce1-4963-8982-62f6dbc690e7 Boho Bedroom Decor Ideas Are you thinking of refreshing your bedroom? Not sure where to start? If you've got something fun and comfortable on The Cards We Drew 64k Small Room Bedroom,Room Ideas Bedroom,Home Bedroom,Small Rooms,Romantic Master Bedroom Ideas,Living Room And Bedroom In One,Cozy Master Bedroom Ideas,Modern Boho Master Bedroom,Dark Master Bedroom image https://i.pinimg.com/originals/cb/36/99/cb3699c00451c4767b94a86843f1013e.jpg 1 Local save in /data/home-decor home-decor 2944 848ab3c9-92ee-4160-a2c4-f8b3babdebd7 Clay Tutorials Pt.4 No description available Story format Myasaurus 2k Diy Crafts To Do,Diy Crafts Hacks,Diy Crafts Jewelry,Diy Bracelets Patterns,Polymer Clay Tools,How To Make Clay,Things To Do When Bored,Indie Room,Cute Clay multi-video(story page format) Image src error. 0 Local save in /data/diy-and-crafts diy-and-crafts 5289 158800d5-44af-4074-928d-96cfea2af35c How To Make Money With Dividends Dividends and dividend stocks are the paths to financial freedom. Find out how much money you need to save and invest to make a million dollars. Then live the life you want whil…  Dividends Diversify: Money Matters So Build Wealth & Be Rich 28k Ways To Earn Money,Earn Money From Home,Money Tips,Way To Make Money,Make Money Online,Investing In Stocks,Investing Money,Saving Money,Dividend Investing image https://i.pinimg.com/originals/f7/f4/43/f7f4434d8cea806a8688df8d411d2fe7.jpg 1 Local save in /data/finance finance 8111 157b5520-b073-47c6-8f63-ab4ee3cdd4af 5 Areas Of Focus For Future Brides Quotes About Wedding : Whatever our souls are made his and mine are the same | Emily Bronte Quote | Literary Wedding | Love Quotes Odyssey 235k Cute Love Quotes,Love Quotes For Wedding,Famous Love Quotes,Romantic Quotes,Classic Love Quotes,Beautiful Quotes About Love,Best Book Quotes,Famous Wedding Quotes,Vintage Love Quotes image https://i.pinimg.com/originals/13/32/37/133237cbeac821ebd1f90dc5c5dde196.jpg 1 Local save in /data/quotes quotes 3888 492b807e-6d41-4a65-8c29-ec14d9cba76a Spelling Rules with Anchor Charts (also bonus Boom Cards) In this pack you will find 8 different spelling rules / anchor charts. Each rule has its own activity sheet to go with it. The pack is suitable for Grades 2 - 5. The posters can…  Teachers Pay Teachers 1M Phonics Chart,Phonics Rules,Spelling Rules,Phonics Wor

In [0]:
# For the geolocation data:
geo_0e1f6d6285c1_df = spark \
.readStream \
.format('kinesis') \
.option('StreamName','streaming-0e1f6d6285c1-geo') \
.option('initialPosition','earliest') \
.option('region','us-east-1') \
.option('awsAccessKey', ACCESS_KEY) \
.option('awsSecretKey', SECRET_KEY) \
.load()

# Displaying the dataframe, this is the data arriving from Kinesis in the default schema of Kinesis: partitionKey, data, stream, shardId, sequenceNnumber, approximateArrivalTimestamp
display(geo_0e1f6d6285c1_df)

partitionKey data stream shardId sequenceNumber approximateArrivalTimestamp geo_partition eyJpbmQiOjYzNjUsInRpbWVzdGFtcCI6IjIwMjItMTAtMTFUMTc6MzQ6NDIiLCJsYXRpdHVkZSI6LTc4LjIxMDQsImxvbmdpdHVkZSI6LTEyMC4yOTIsImNvdW50cnkiOiJDaHJpc3RtYXMgSXNsYW5kIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781674444871826857202999690788866 2023-10-18T14:17:37.247+0000 geo_partition eyJpbmQiOjk4MTUsInRpbWVzdGFtcCI6IjIwMTktMDMtMDJUMDY6NTQ6MTQiLCJsYXRpdHVkZSI6LTEwLjc2MjEsImxvbmdpdHVkZSI6LTE3NS45ODUsImNvdW50cnkiOiJDb25nbyJ9 streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781676516970681676677611295604738 2023-10-18T14:17:39.652+0000 geo_partition eyJpbmQiOjcwOTAsInRpbWVzdGFtcCI6IjIwMjItMDEtMDhUMTg6NTM6NTIiLCJsYXRpdHVkZSI6LTYyLjkyLCJsb25naXR1ZGUiOi02My43OTc0LCJjb3VudHJ5IjoiQW50YXJjdGljYSAodGhlIHRlcnJpdG9yeSBTb3V0aCA= (truncated) streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781678421028847569718698896785410 2023-10-18T14:17:42.118+0000 geo_partition eyJpbmQiOjQzNTMsInRpbWVzdGFtcCI6IjIwMTgtMDItMDNUMjM6MTg6MDMiLCJsYXRpdHVkZSI6MTUuNTU1MywibG9uZ2l0dWRlIjotNTUuNDgwNiwiY291bnRyeSI6IkNvbmdvIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781679585224411858606662858309634 2023-10-18T14:17:43.474+0000 geo_partition eyJpbmQiOjMxMDgsInRpbWVzdGFtcCI6IjIwMjAtMTAtMTVUMTI6NTQ6MjciLCJsYXRpdHVkZSI6LTczLjU4OCwibG9uZ2l0dWRlIjotMTQ2LjUzNywiY291bnRyeSI6IkRqaWJvdXRpIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781680702271869182524157725769730 2023-10-18T14:17:44.837+0000 geo_partition eyJpbmQiOjI5NjMsInRpbWVzdGFtcCI6IjIwMjAtMTEtMTRUMTg6MzY6MjUiLCJsYXRpdHVkZSI6MTUuMzU4NiwibG9uZ2l0dWRlIjotODQuMDMyMiwiY291bnRyeSI6Ik5vcmZvbGsgSXNsYW5kIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781682593031851059804324405182466 2023-10-18T14:17:47.187+0000 geo_partition eyJpbmQiOjEwODEzLCJ0aW1lc3RhbXAiOiIyMDE4LTA1LTI1VDE3OjMzOjEwIiwibGF0aXR1ZGUiOi04NS44Njk5LCJsb25naXR1ZGUiOi0xOC4zNTc0LCJjb3VudHJ5IjoiRG9taW5pY2FuIFJlcHVibGljIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781683808002299772506782423842818 2023-10-18T14:17:48.577+0000 geo_partition eyJpbmQiOjM0MTcsInRpbWVzdGFtcCI6IjIwMTgtMDItMDZUMTM6NDE6MTkiLCJsYXRpdHVkZSI6LTQ1LjgxODMsImxvbmdpdHVkZSI6NS40MDI4LCJjb3VudHJ5IjoiTHV4ZW1ib3VyZyJ9 streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781685570616144770636325303877634 2023-10-18T14:17:50.926+0000 geo_partition eyJpbmQiOjMwOTAsInRpbWVzdGFtcCI6IjIwMTktMDgtMDVUMDc6MzI6MjEiLCJsYXRpdHVkZSI6MjguNTM0NywibG9uZ2l0dWRlIjoxNjQuNzIzLCJjb3VudHJ5IjoiUG9ydHVnYWwifQ== streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781686751736670534129097711288322 2023-10-18T14:17:52.395+0000 geo_partition eyJpbmQiOjU0NTEsInRpbWVzdGFtcCI6IjIwMTktMTEtMDdUMDY6MDQ6NDQiLCJsYXRpdHVkZSI6LTU4LjYyOCwibG9uZ2l0dWRlIjotMTI4Ljk5NCwiY291bnRyeSI6IkJhaGFtYXMifQ== streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781687805919985238085806774550530 2023-10-18T14:17:53.724+0000 geo_partition eyJpbmQiOjY4MTMsInRpbWVzdGFtcCI6IjIwMTktMDMtMjhUMDk6MzQ6MDYiLCJsYXRpdHVkZSI6LTg5Ljk3ODcsImxvbmdpdHVkZSI6LTE3My4yOTMsImNvdW50cnkiOiJBbGJhbmlhIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781688722285756505974789921308674 2023-10-18T14:17:55.053+0000 geo_partition eyJpbmQiOjEwMDAyLCJ0aW1lc3RhbXAiOiIyMDIwLTA5LTEzVDE1OjAxOjUyIiwibGF0aXR1ZGUiOjcxLjc4ODQsImxvbmdpdHVkZSI6MTQ4Ljk2OCwiY291bnRyeSI6Ik5ldGhlcmxhbmRzIEFudGlsbGVzIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781689920331243744072370774605826 2023-10-18T14:17:56.467+0000 geo_partition eyJpbmQiOjI0NTMsInRpbWVzdGFtcCI6IjIwMjItMDctMDRUMDQ6NTU6MTYiLCJsYXRpdHVkZSI6LTcyLjg4NzksImxvbmdpdHVkZSI6LTEzMS45NjYsImNvdW50cnkiOiJCcml0aXNoIFZpcmdpbiBJc2xhbmRzIn0= streaming-0e1f6d6285c1-geo shardId-000000000000 49645428141191709353378781691895716032994376648402927618 2023-10-18T14:17:58.845+0000 geo_partiti

In [0]:
# To see the data contained in the geolocation stream, we need to deserialise the data column of the dataframe above:
geo_0e1f6d6285c1_df = geo_0e1f6d6285c1_df.selectExpr("CAST(data as STRING)")

# Displaying the dataframe:
display(geo_0e1f6d6285c1_df)

data {"ind":2225,"timestamp":"2019-08-20T23:00:52","latitude":-85.7998,"longitude":-109.58,"country":"American Samoa"} {"ind":4616,"timestamp":"2020-12-28T07:29:40","latitude":-53.5421,"longitude":-110.613,"country":"Pakistan"} {"ind":649,"timestamp":"2020-10-06T14:24:08","latitude":-80.7952,"longitude":-22.2518,"country":"Sudan"} {"ind":350,"timestamp":"2020-07-25T07:39:25","latitude":-48.665,"longitude":-77.0735,"country":"El Salvador"} {"ind":3135,"timestamp":"2022-02-28T05:15:42","latitude":-42.578,"longitude":-156.509,"country":"Haiti"} {"ind":10353,"timestamp":"2017-10-19T23:59:57","latitude":-63.1226,"longitude":-176.877,"country":"Guam"} {"ind":1352,"timestamp":"2021-02-27T01:41:15","latitude":60.8783,"longitude":63.8289,"country":"Armenia"} {"ind":8378,"timestamp":"2022-09-29T14:41:43","latitude":-87.2,"longitude":-177.109,"country":"Albania"} {"ind":2215,"timestamp":"2022-08-19T09:07:21","latitude":66.9713,"longitude":163.126,"country":"Yemen"} {"ind":6487,"timestamp":"2018-07-29T05:27:08","latitude":-5.34445,"longitude":-177.924,"country":"Armenia"} {"ind":4661,"timestamp":"2017-12-27T08:27:16","latitude":-89.3666,"longitude":-66.5294,"country":"Heard Island and McDonald Islands"} {"ind":9376,"timestamp":"2021-08-09T08:59:15","latitude":-71.5025,"longitude":-179.257,"country":"Aruba"} {"ind":3912,"timestamp":"2018-01-05T19:48:28","latitude":-47.953,"longitude":-176.463,"country":"Bulgaria"} {"ind":4034,"timestamp":"2019-10-25T20:17:43","latitude":-76.7399,"longitude":-170.18,"country":"Argentina"} {"ind":2349,"timestamp":"2022-03-29T19:48:01","latitude":36.0731,"longitude":-30.6524,"country":"Serbia"} {"ind":10773,"timestamp":"2018-05-26T23:15:41","latitude":-32.1769,"longitude":-114.073,"country":"Bangladesh"} {"ind":1407,"timestamp":"2020-04-11T17:20:28","latitude":-44.9165,"longitude":-61.5849,"country":"New Zealand"} {"ind":4977,"timestamp":"2020-10-05T23:28:10","latitude":-63.0063,"longitude":-157.474,"country":"Azerbaijan"} {"ind":1787,"timestamp":"2018-04-09T13:57:16","latitude":51.7583,"longitude":-62.785,"country":"Malawi"} {"ind":2399,"timestamp":"2022-08-26T07:16:09","latitude":-69.0778,"longitude":-139.194,"country":"Anguilla"} {"ind":1524,"timestamp":"2018-08-31T13:48:12","latitude":-42.7166,"longitude":-126.047,"country":"Algeria"} {"ind":7558,"timestamp":"2018-12-25T06:41:37","latitude":-89.246,"longitude":55.2097,"country":"Cayman Islands"} {"ind":4440,"timestamp":"2022-06-08T08:49:35","latitude":-79.4527,"longitude":-142.801,"country":"Djibouti"} {"ind":4827,"timestamp":"2021-11-29T23:59:01","latitude":47.9307,"longitude":91.4507,"country":"Eritrea"} {"ind":10299,"timestamp":"2021-10-25T19:46:47","latitude":-77.5092,"longitude":-33.8585,"country":"Belgium"} {"ind":8669,"timestamp":"2022-10-13T21:43:39","latitude":0.209602,"longitude":94.7738,"country":"San Marino"} {"ind":8137,"timestamp":"2018-08-23T13:02:42","latitude":-71.6036,"longitude":-175.3,"country":"Argentina"} {"ind":4547,"timestamp":"2018-01-18T12:52:05","latitude":-2.10996,"longitude":-64.2402,"country":"Falkland Islands (Malvinas)"} {"ind":9366,"timestamp":"2020-12-05T02:46:09","latitude":-84.7363,"longitude":-179.087,"country":"Andorra"} {"ind":6834,"timestamp":"2019-08-25T15:54:59","latitude":-60.0697,"longitude":-109.639,"country":"Nauru"} {"ind":9442,"timestamp":"2020-09-01T00:07:36","latitude":36.0482,"longitude":19.362,"country":"Tonga"} {"ind":8853,"timestamp":"2021-05-22T09:46:13","latitude":-88.5228,"longitude":-66.5601,"country":"Angola"} {"ind":5182,"timestamp":"2020-09-08T05:45:04","latitude":77.1581,"longitude":-53.8123,"country":"Botswana"} {"ind":2315,"timestamp":"2019-06-05T08:54:04","latitude":17.806,"longitude":-1.9042,"country":"Guinea-Bissau"} {"ind":6206,"timestamp":"2019-08-05T21:00:44","latitude":-74.2018,"longitude":-145.739,"country":"Syrian Arab Republic"} {"ind":9194,"timestamp":"2021-09-22T19:11:26","latitude":-88.5313,"longitude":-174.647,"country":"Bahamas"} {"ind":4365,"timestamp":"2019-06-14T18:38:28","l

In [0]:
# Converting the above datarame which contains strings for each row into its constituent coloumns and values:
# Defining the schema for the JSON data, the schema specifies the expected data types of each JSON field:
geo_json_schema = StructType([
    StructField("ind", IntegerType(), True),
    StructField("timestamp", TimestampType(), True),
    StructField("latitude", FloatType(), True),
    StructField("longitude", FloatType(), True),
    StructField("country", StringType(), True),    
])

# Using the from_json function, parse the JSON strings in the "data" column above according to the geo data schema defined above:
geo_parsed_df = geo_0e1f6d6285c1_df.withColumn("geo_parsed_data", from_json(col("data"), geo_json_schema))

# Selecting the values of each column from the parsed geo dataframe:
geo_E_0e1f6d6285c1_df = geo_parsed_df.select(
    col("geo_parsed_data.ind").alias("ind"),
    col("geo_parsed_data.timestamp").alias("timestamp"),
    col("geo_parsed_data.latitude").alias("latitude"),
    col("geo_parsed_data.longitude").alias("longitude"),
    col("geo_parsed_data.country").alias("country")
)

# Showing the resulting geo dataframe:
display(geo_E_0e1f6d6285c1_df)

ind timestamp latitude longitude country 8388 2018-10-26T02:37:43.000+0000 -89.5173 -179.689 Algeria 4059 2022-05-09T08:09:29.000+0000 -85.4776 -130.258 British Indian Ocean Territory (Chagos Archipelago) 5095 2021-10-28T21:55:36.000+0000 -73.6474 39.8754 Ireland 8695 2021-01-14T01:06:27.000+0000 -84.3984 -144.933 Bouvet Island (Bouvetoya) 594 2020-10-01T21:21:05.000+0000 -58.4025 -168.097 Albania 7276 2018-08-03T05:14:15.000+0000 -58.4743 21.875 Sweden 6198 2022-04-25T07:46:15.000+0000 32.8838 -149.384 Morocco 7666 2021-02-06T19:47:52.000+0000 -89.5173 -179.689 Algeria 2582 2020-01-21T22:47:21.000+0000 -63.5778 -31.1543 Bangladesh 9611 2020-07-06T19:36:55.000+0000 64.733 -2.5288 Thailand 5645 2019-02-28T17:19:17.000+0000 -85.9781 -172.038 Indonesia 5843 2018-02-13T22:01:38.000+0000 5.50681 -170.017 Bosnia and Herzegovina 2343 2019-10-15T13:21:45.000+0000 60.6981 -79.5945 Brazil 2188 2022-05-11T15:29:49.000+0000 45.2136 -120.461 Greenland 328 2021-09-11T11:17:22.000+0000 -52.7867 -53.6215 Christmas Island 7934 2021-05-18T22:57:23.000+0000 -87.0949 -124.759 Costa Rica 4692 2019-09-21T10:39:12.000+0000 -89.1633 -159.957 Austria 7619 2020-07-04T10:36:23.000+0000 -87.8179 -178.525 Afghanistan 7030 2022-03-04T10:30:19.000+0000 -88.3754 -164.273 Afghanistan 4241 2018-10-15T02:28:54.000+0000 -88.5478 -174.971 Afghanistan 7567 2021-08-14T03:32:29.000+0000 7.94397 168.552 Argentina 6146 2020-11-29T23:26:48.000+0000 -86.2476 -171.577 Aruba 4359 2018-08-22T16:24:09.000+0000 -64.7814 42.1051 New Caledonia 5836 2022-01-11T06:17:42.000+0000 -62.7034 -114.366 Albania 7195 2020-12-16T07:09:08.000+0000 -62.0138 107.319 Lebanon 4535 2021-03-06T10:08:48.000+0000 89.9306 89.7625 Tuvalu 2667 2019-12-13T06:24:00.000+0000 -89.0609 -170.904 Anguilla 8875 2020-11-28T03:11:49.000+0000 -84.7363 -179.087 Andorra 7415 2022-03-24T00:04:08.000+0000 -88.5425 -157.374 Central African Republic 3920 2021-09-19T12:31:46.000+0000 -10.1583 -110.372 Belarus 747 2021-03-11T15:28:22.000+0000 -84.8378 -167.14 Aruba 7372 2020-01-16T19:12:43.000+0000 -59.5694 -94.3721 Cote d'Ivoire 2690 2019-01-03T19:42:56.000+0000 39.0536 -36.7319 Kiribati 10389 2018-09-26T02:46:48.000+0000 -89.1005 -151.255 Burkina Faso 6427 2018-06-21T07:15:28.000+0000 -59.588 40.3966 Andorra 6545 2018-12-14T06:27:48.000+0000 -62.9651 -164.763 Albania 796 2019-12-21T04:30:01.000+0000 -88.8298 -170.188 Albania 8214 2022-02-24T03:29:23.000+0000 -89.5173 -179.689 Algeria 4610 2018-07-03T13:22:20.000+0000 -78.397 104.319 Macao 3246 2020-04-14T05:30:25.000+0000 -84.5322 -179.647 Afghanistan 9182 2020-12-25T14:14:42.000+0000 84.2884 -150.532 Canada 3559 2018-05-02T21:38:31.000+0000 -85.9127 -158.979 British Virgin Islands 18 2021-02-21T22:02:59.000+0000 -77.6883 -145.539 Andorra 9655 2019-08-26T02:21:40.000+0000 -3.38187 66.843 Latvia 4927 2022-02-05T01:32:57.000+0000 -82.0592 -92.7514 Aruba 8440 2019-10-08T22:45:50.000+0000 -23.9898 -45.1618 New Caledonia 6712 2021-05-10T20:22:50.000+0000 -73.274 -175.376 Colombia 1324 2019-10-28T01:24:28.000+0000 -10.2532 -124.71 Netherlands Antilles 5253 2018-02-18T17:51:22.000+0000 -73.8133 -103.692 Cameroon 2579 2021-01-08T15:40:31.000+0000 -54.336 -130.459 Belarus 6563 2019-03-20T16:52:51.000+0000 33.9419 112.435 Thailand 6568 2021-08-27T23:43:21.000+0000 -87.4286 -141.383 Afghanistan 2819 2018-07-04T18:48:23.000+0000 -84.8365 -122.171 French Polynesia 7902 2022-04-13T15:57:13.000+0000 -87.8179 -178.525 Afghanistan 10323 2018-02-24T02:37:17.000+0000 46.4699 -65.2662 Malawi 1122 2021-07-29T01:12:55.000+0000 -54.9169 -93.8569 Gibraltar 1568 2020-07-09T01:20:01.000+0000 -41.7803 -177.23 Argentina 8559 2019-04-19T03:56:11.000+0000 -88.5255 -161.644 American Samoa 9156 2021-01-04T04:20:11.000+0000 -78.312 -134.376 Belize 4649 2022-08-18T11:15:02.000+0000 -48.2064 -176.272 Bahamas 895 2018-01-05T19:02:36.000+0000 -55.2327 -104.093 Congo 6264 2019-06-09T00:01:11.000+0000 -72.5021 -128.903 Finland 8794 2022-10-10T13:06:54.000+0000 -84.7363 -179.087 Andorra 2838 2020-09-15T15

In [0]:
# For the user data:
user_0e1f6d6285c1_df = spark \
.readStream \
.format('kinesis') \
.option('StreamName','streaming-0e1f6d6285c1-user') \
.option('initialPosition','earliest') \
.option('region','us-east-1') \
.option('awsAccessKey', ACCESS_KEY) \
.option('awsSecretKey', SECRET_KEY) \
.load()

# Displaying the dataframe, this is the data arriving from Kinesis in the default schema of Kinesis: partitionKey, data, stream, shardId, sequenceNnumber, approximateArrivalTimestamp
display(user_0e1f6d6285c1_df)

partitionKey data stream shardId sequenceNumber approximateArrivalTimestamp user_partition eyJpbmQiOjEwODEzLCJmaXJzdF9uYW1lIjoiQW5pdGEiLCJsYXN0X25hbWUiOiJNb29yZSIsImFnZSI6MjAsImRhdGVfam9pbmVkIjoiMjAxNi0wMy0wNFQxMDoxMDo0NSJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511545544367101473160574120493106 2023-10-18T14:17:48.211+0000 user_partition eyJpbmQiOjM0MTcsImZpcnN0X25hbWUiOiJTYXJhaCIsImxhc3RfbmFtZSI6IkZveCIsImFnZSI6NDksImRhdGVfam9pbmVkIjoiMjAxNy0xMC0xMVQyMzo1NTozOCJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511546839126654280428695108714546 2023-10-18T14:17:50.580+0000 user_partition eyJpbmQiOjMwOTAsImZpcnN0X25hbWUiOiJKb3ljZSIsImxhc3RfbmFtZSI6IkdvcmRvbiIsImFnZSI6MzksImRhdGVfam9pbmVkIjoiMjAxNy0wOC0wMlQxOTowNjoxMSJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511547662405137437991231803097138 2023-10-18T14:17:52.042+0000 user_partition eyJpbmQiOjU0NTEsImZpcnN0X25hbWUiOiJBbWJlciIsImxhc3RfbmFtZSI6IkVyaWNrc29uIiwiYWdlIjoyNiwiZGF0ZV9qb2luZWQiOiIyMDE1LTExLTA3VDA5OjU3OjU1In0= streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511548375671371010622513599217714 2023-10-18T14:17:53.368+0000 user_partition eyJpbmQiOjY4MTMsImZpcnN0X25hbWUiOiJBYmlnYWlsIiwibGFzdF9uYW1lIjoiQWxpIiwiYWdlIjoyMCwiZGF0ZV9qb2luZWQiOiIyMDE1LTEwLTI0VDExOjIzOjUxIn0= streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511549044207349257512515931209778 2023-10-18T14:17:54.699+0000 user_partition eyJpbmQiOjEwMDAyLCJmaXJzdF9uYW1lIjoiTWljaGVsbGUiLCJsYXN0X25hbWUiOiJHYXJjaWEiLCJhZ2UiOjMxLCJkYXRlX2pvaW5lZCI6IjIwMTYtMDItMjdUMjI6NDM6NTcifQ== streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511549773189618485133976998510642 2023-10-18T14:17:56.036+0000 user_partition eyJpbmQiOjI0NTMsImZpcnN0X25hbWUiOiJDYXRoZXJpbmUiLCJsYXN0X25hbWUiOiJCdXJrZSIsImFnZSI6MjcsImRhdGVfam9pbmVkIjoiMjAxNi0wNC0wOVQwMjowODoxMyJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511551167081088500801621593161778 2023-10-18T14:17:58.458+0000 user_partition eyJpbmQiOjU2MzYsImZpcnN0X25hbWUiOiJNYWNrZW56aWUiLCJsYXN0X25hbWUiOiJFc3RlcyIsImFnZSI6MjksImRhdGVfam9pbmVkIjoiMjAxNi0wNS0wMlQwMDo1MDo0MCJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511552602076036383366589408346162 2023-10-18T14:18:01.033+0000 user_partition eyJpbmQiOjEzMzgsImZpcnN0X25hbWUiOiJHcmVnb3J5IiwibGFzdF9uYW1lIjoiQmFybmV0dCIsImFnZSI6MjAsImRhdGVfam9pbmVkIjoiMjAxNi0wMy0yOVQxNzoxMDowMyJ9 streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511553386668893313261061231607858 2023-10-18T14:18:02.384+0000 user_partition eyJpbmQiOjQyOTUsImZpcnN0X25hbWUiOiJBbGV4YW5kcmlhIiwibGFzdF9uYW1lIjoiQWx2YXJhZG8iLCJhZ2UiOjIwLCJkYXRlX2pvaW5lZCI6IjIwMTUtMTAtMjNUMDQ6MTM6MjMifQ== streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511554735830108003187357642653746 2023-10-18T14:18:04.807+0000 user_partition eyJpbmQiOjk0OTgsImZpcnN0X25hbWUiOiJBcHJpbCIsImxhc3RfbmFtZSI6IkdhcmRuZXIiLCJhZ2UiOjMxLCJkYXRlX2pvaW5lZCI6IjIwMTUtMTEtMTlUMDU6MzY6NTAifQ== streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511556176869684983825471331369010 2023-10-18T14:18:07.190+0000 user_partition eyJpbmQiOjUzMjgsImZpcnN0X25hbWUiOiJMYW5jZSIsImxhc3RfbmFtZSI6IlNtaXRoIiwiYWdlIjoyOCwiZGF0ZV9qb2luZWQiOiIyMDE2LTAxLTI2VDA1OjMzOjE5In0= streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511557504270234920688511317180466 2023-10-18T14:18:09.617+0000 user_partition eyJpbmQiOjEwNDY4LCJmaXJzdF9uYW1lIjoiQ29yeSIsImxhc3RfbmFtZSI6IlBlcmV6IiwiYWdlIjo0NCwiZGF0ZV9qb2luZWQiOiIyMDE2LTAxLTI3VDA1OjQ2OjAzIn0= streaming-0e1f6d6285c1-user shardId-000000000003 49645429742987334728239511558705942499617630048414072882 2023-10-18T14:18:12.070+0000 user_partition eyJpbmQiOjEwNDY0LCJmaXJzdF9uYW1lIjoiSmVubmlmZXIiLCJsYXN0X25hbWUiOiJIaWxsIiwiYWdlIjozMiwiZGF0ZV9qb2luZWQiOiIyMDE2LTA0LTIwVDE3OjQ4OjQ4In0= streaming-0e1f6d6285c1-user shardId-000000000003 49645429

In [0]:
# To see the data contained in the user stream, we need to deserialise the data column of the dataframe above:
user_0e1f6d6285c1_df = user_0e1f6d6285c1_df.selectExpr("CAST(data as STRING)")

# Displaying the dataframe:
display(user_0e1f6d6285c1_df)

data {"ind":2215,"first_name":"Collin","last_name":"Nolan","age":21,"date_joined":"2017-07-15T18:25:40"} {"ind":6487,"first_name":"Dylan","last_name":"Holmes","age":32,"date_joined":"2016-10-23T14:06:51"} {"ind":4661,"first_name":"Brandy","last_name":"Nolan","age":39,"date_joined":"2017-02-16T02:20:16"} {"ind":9376,"first_name":"Amy","last_name":"Adams","age":20,"date_joined":"2015-10-24T05:05:28"} {"ind":3912,"first_name":"Antonio","last_name":"Davis","age":21,"date_joined":"2015-12-05T06:09:18"} {"ind":4034,"first_name":"Amanda","last_name":"Bennett","age":23,"date_joined":"2016-07-26T16:57:11"} {"ind":2349,"first_name":"Jaclyn","last_name":"Browning","age":30,"date_joined":"2016-02-05T19:15:02"} {"ind":10773,"first_name":"April","last_name":"Davis","age":26,"date_joined":"2016-05-17T22:11:51"} {"ind":1407,"first_name":"Jason","last_name":"Morales","age":58,"date_joined":"2017-07-03T19:30:09"} {"ind":4977,"first_name":"Amanda","last_name":"Ball","age":25,"date_joined":"2016-01-13T17:36:30"} {"ind":1787,"first_name":"Christopher","last_name":"Park","age":25,"date_joined":"2016-01-06T23:12:49"} {"ind":2399,"first_name":"Jonathan","last_name":"Garcia","age":31,"date_joined":"2016-01-18T15:20:06"} {"ind":1524,"first_name":"Daniel","last_name":"Baldwin","age":23,"date_joined":"2016-01-11T05:33:09"} {"ind":7558,"first_name":"Carl","last_name":"Daniels","age":20,"date_joined":"2015-12-22T13:01:18"} {"ind":4440,"first_name":"Brooke","last_name":"Brown","age":35,"date_joined":"2016-03-24T12:29:52"} {"ind":4827,"first_name":"Dana","last_name":"Ellis","age":57,"date_joined":"2016-02-06T08:50:41"} {"ind":10299,"first_name":"Jennifer","last_name":"Kaiser","age":30,"date_joined":"2015-11-24T03:29:52"} {"ind":8669,"first_name":"Michael","last_name":"Kelly","age":43,"date_joined":"2016-12-30T00:49:44"} {"ind":8137,"first_name":"Diana","last_name":"Barry","age":26,"date_joined":"2015-11-12T15:36:01"} {"ind":4547,"first_name":"Rebecca","last_name":"Bailey","age":35,"date_joined":"2016-06-01T08:35:00"} {"ind":9366,"first_name":"Aaron","last_name":"Alexander","age":21,"date_joined":"2015-10-25T07:36:08"} {"ind":6834,"first_name":"Keith","last_name":"Martinez","age":38,"date_joined":"2015-11-17T12:56:37"} {"ind":9442,"first_name":"Jamie","last_name":"Carey","age":37,"date_joined":"2015-11-19T02:36:08"} {"ind":8853,"first_name":"Christopher","last_name":"Ball","age":21,"date_joined":"2015-12-26T13:32:59"} {"ind":5182,"first_name":"Jonathon","last_name":"Crawford","age":25,"date_joined":"2016-12-09T04:56:37"} {"ind":2315,"first_name":"Ashley","last_name":"Briggs","age":38,"date_joined":"2015-11-15T16:53:09"} {"ind":6206,"first_name":"Susan","last_name":"Harris","age":45,"date_joined":"2016-04-24T17:05:50"} {"ind":9194,"first_name":"Adam","last_name":"Burns","age":20,"date_joined":"2015-11-27T16:06:53"} {"ind":4365,"first_name":"Rebecca","last_name":"Bailey","age":35,"date_joined":"2016-06-01T08:35:00"} {"ind":7647,"first_name":"Aaron","last_name":"Abbott","age":20,"date_joined":"2015-10-23T16:08:41"} {"ind":9198,"first_name":"Amber","last_name":"Chen","age":22,"date_joined":"2015-12-30T05:21:14"} {"ind":10869,"first_name":"Claudia","last_name":"Adams","age":20,"date_joined":"2015-11-28T02:20:29"} {"ind":10175,"first_name":"Annette","last_name":"Andrews","age":28,"date_joined":"2015-12-20T22:09:10"} {"ind":6444,"first_name":"David","last_name":"Taylor","age":23,"date_joined":"2016-04-24T07:53:10"} {"ind":1812,"first_name":"Barbara","last_name":"Brown","age":28,"date_joined":"2016-05-13T14:12:27"} {"ind":3896,"first_name":"Alexandria","last_name":"Alvarado","age":20,"date_joined":"2015-10-23T04:13:23"} {"ind":3266,"first_name":"Robert","last_name":"Golden","age":50,"date_joined":"2017-03-19T15:29:02"} {"ind":7026,"first_name":"Abigail","last_name":"Ali","age":20,"date_joined":"2015-10-24T11:23:51"} {"ind":4384,"first_name":"Aaron","last_name":"Abbott","age":20,"date_joined":"2015-10-31T18:51:07"} {"ind":581,"first_name":"Adam","last_name":"Acosta","

In [0]:
# Converting the above datarame which contains strings for each row into its constituent coloumns and values:
# Defining the schema for the JSON data, the schema specifies the expected data types of each JSON field:
user_json_schema = StructType([
    StructField("ind", IntegerType(), True),
    StructField("first_name", StringType(), True),
    StructField("last_name", StringType(), True),
    StructField("age", IntegerType(), True),
    StructField("date_joined", TimestampType(), True),    
])

# Using the from_json function, parse the JSON strings in the "data" column above according to the user data schema defined above:
user_parsed_df = user_0e1f6d6285c1_df.withColumn("user_parsed_data", from_json(col("data"), user_json_schema))

# Selecting the values of each column from the parsed user dataframe:
user_E_0e1f6d6285c1_df = user_parsed_df.select(
    col("user_parsed_data.ind").alias("ind"),
    col("user_parsed_data.first_name").alias("first_name"),
    col("user_parsed_data.last_name").alias("last_name"),
    col("user_parsed_data.age").alias("age"),
    col("user_parsed_data.date_joined").alias("date_joined")
)

# Showing the resulting user dataframe:
display(user_E_0e1f6d6285c1_df)

ind first_name last_name age date_joined 4241 Alexandria Alvarado 20 2015-10-23T04:13:23.000+0000 7567 Mark Russell 56 2017-05-18T20:35:15.000+0000 6146 Adrian Allen 21 2015-10-21T22:43:58.000+0000 4359 Jason Barnes 27 2017-07-10T21:06:14.000+0000 5836 Brian Davis 38 2015-12-09T10:50:57.000+0000 7195 Amber Barnes 32 2017-08-14T00:57:09.000+0000 4535 Michael Snyder 51 2017-07-22T13:03:59.000+0000 2667 Amber Casey 23 2016-01-06T12:22:08.000+0000 8875 Aaron Alexander 21 2015-10-25T07:36:08.000+0000 7415 April Anderson 30 2016-06-27T08:35:51.000+0000 3920 Valerie Burke 32 2017-08-01T19:20:34.000+0000 747 Amanda Alvarez 21 2015-10-30T01:31:09.000+0000 7372 Michelle Miller 31 2015-10-21T07:41:23.000+0000 2690 Robert Robertson 29 2016-11-05T17:30:14.000+0000 10389 Andrea Burke 20 2015-12-12T11:20:08.000+0000 6427 Christopher Montgomery 28 2015-11-24T22:47:19.000+0000 6545 Amanda Carter 23 2015-11-30T08:07:07.000+0000 796 Adam Acosta 20 2015-10-21T21:26:45.000+0000 8214 Aaron Abbott 20 2015-10-23T16:08:41.000+0000 4610 Jesse Wagner 22 2016-12-22T01:34:50.000+0000 3246 Abigail Adams 20 2015-10-25T13:11:51.000+0000 9182 Margaret Henry 51 2017-08-12T22:51:22.000+0000 3559 Anne Atkins 23 2016-04-01T03:19:05.000+0000 18 Brandon Holmes 21 2015-11-02T23:30:01.000+0000 9655 Michael Arnold 42 2017-06-24T09:04:07.000+0000 4927 Abigail Barry 21 2015-12-03T10:40:24.000+0000 8440 Lindsey Graham 44 2015-10-27T13:38:10.000+0000 6712 Brian Johnson 20 2016-04-22T16:08:34.000+0000 1324 Patrick Davidson 41 2016-12-24T11:07:22.000+0000 5253 Amy Brown 21 2017-04-03T19:28:27.000+0000 2579 Alexandra Brown 21 2015-11-05T07:52:21.000+0000 6563 Amanda Hill 52 2016-09-29T22:35:49.000+0000 6568 Christopher Allen 23 2016-01-16T20:10:28.000+0000 2819 David Bell 20 2016-04-15T17:11:11.000+0000 7902 Andrew Alexander 20 2015-11-20T09:08:00.000+0000 10323 Christina Garrett 29 2016-03-25T18:05:18.000+0000 1122 Cassandra Barnes 34 2016-05-15T02:50:09.000+0000 1568 Donna Campbell 32 2016-06-08T22:10:13.000+0000 8559 Alexander Bailey 20 2015-10-30T11:37:32.000+0000 9156 Christopher Bass 32 2016-06-24T18:45:25.000+0000 4649 Amber Bennett 29 2016-02-28T04:37:04.000+0000 895 Andrew Hebert 30 2016-06-23T04:14:51.000+0000 6264 Antonio Aguilar 42 2015-11-16T00:07:37.000+0000 8794 Aaron Alexander 21 2015-10-25T07:36:08.000+0000 2838 Melissa Schneider 56 2015-11-13T16:02:50.000+0000 3466 Christopher Green 34 2016-09-17T04:22:25.000+0000 783 Aaron Bartlett 21 2015-11-24T02:15:36.000+0000 3843 Ronald Hanson 28 2017-04-16T00:14:21.000+0000 2587 Daniel Doyle 23 2015-10-28T04:22:38.000+0000 10093 Jamie Andrews 46 2016-10-11T07:57:59.000+0000 910 Alexandria Davis 27 2016-02-24T12:13:37.000+0000 4990 Kelly Alexander 38 2015-10-27T12:47:27.000+0000 2871 Jessica Gardner 39 2016-01-02T11:00:04.000+0000 5580 Adam Cole 23 2015-11-15T23:49:12.000+0000 5399 Calvin Atkins 27 2016-08-31T20:20:25.000+0000 7915 Angela Pearson 56 2017-08-17T14:31:27.000+0000 7808 Deborah Madden 28 2015-11-19T19:21:56.000+0000 846 Andres Cortez 26 2015-11-20T21:50:39.000+0000 6180 Carolyn Bell 57 2016-05-15T19:11:25.000+0000 1740 Richard Stewart 59 2015-11-20T04:51:19.000+0000 9307 Adam Acosta 20 2015-10-21T21:26:45.000+0000 5097 Adam Alexander 20 2015-10-22T11:31:37.000+0000 2094 Amanda Gutierrez 28 2017-04-22T05:41:06.000+0000 1011 April Casey 23 2015-11-09T11:31:53.000+0000 7277 Frank Bates 23 2016-01-12T00:57:43.000+0000 7709 Aaron Abbott 20 2015-10-23T16:08:41.000+0000 9704 Kimberly Lindsey 28 2016-04-18T12:44:41.000+0000 301 Amanda Alvarez 21 2015-10-30T01:31:09.000+0000 6608 Amber Boone 44 2016-06-27T19:54:43.000+0000 7186 Alvin Adams 20 2016-01-01T13:50:40.000+0000 4547 Rebecca Bailey 35 2016-06-01T08:35:00.000+0000 2911 Cory Hopkins 44 2016-08-16T11:38:08.000+0000 2275 Andrew Buck 23 2016-01-06T23:14:16.000+0000 5618 Jeffrey Anderson 59 2016-09-30T16:23:46.000+0000 10434 Jacqueline Taylor 37 2017-01-17T05:17:36.000+0000 8156 Amanda Adams 20 2015-10-21T08:27:36.000+0000 1226 Gina Hanson 29 2017-01-07T17:13:3

## Transforming the incoming three streams to ensure the data is clean and ready for analytics

### Transforming the Pinterest posts data:

In [0]:
# Renaming the 'index' column to 'ind':
pin_T_0e1f6d6285c1_df = pin_E_0e1f6d6285c1_df.withColumnRenamed("index", "ind")

In [0]:
# Reordering the columns in the dataframe (whilst omitting the 'downloaded' column):
# new desired order of columns:
desired_pin_column_order = ["ind", "unique_id", "title", "description", "follower_count", "poster_name", "tag_list", "is_image_or_video", "image_src", "save_location", "category"]

pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.select(desired_pin_column_order)

In [0]:
# Whilst performing a simple count on distinct values in the 'follower_count' column there were several hits for 'User Info Error'. Upon further investigation, the entire row of data is not useful so to drop these rows in the dataframe:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.filter(col("follower_count") != "User Info Error")

In [0]:
# Whilst performing a simple count on distinct values in the 'ind' column, results show that there are several identical rows of data, to drop these duplicates:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.dropDuplicates(["ind"])

In [0]:
# During EDA, the 'follower_count' column has values such as '10k, 500, 100k, 2M' so we need to turn all of these into integers:
# Create a custom user defined function (UDF) to remove the "k" and "M" from the 'follower_count' column and return an integer equivalent:

# First, defining a custom UDF to convert 'follower_count to integers and anything containing "k" in the values to integers:
def convert_follower_count(value):
    if 'M' in value:
        return int(value.strip('M')) * 1000000
    elif 'k' in value:
        return int(value.strip('k')) * 1000
    else:
        return int(value)

# Registering the UDF in Spark with function:
convert_follower_count_udf = udf(convert_follower_count)

# Applying the UDF to the "follower_count" column
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("follower_count", convert_follower_count_udf(col("follower_count")))

# Casting the 'follower_count' column to integer data type:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("follower_count", col("follower_count").cast("integer"))

In [0]:
# The "save_location" should only contain the the path location path so need to removed the prefix to this column:
# Creating a custom UDF to remove the "Local save in " of each row in the column:

def remove_prefix_save_location(value):
        return value.replace('Local save in ', '')
    
# Registering the UDF in Spark with function:
remove_prefix_save_location_udf = udf(remove_prefix_save_location)

# Applying the UDF to the "save_location" column
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("save_location", remove_prefix_save_location_udf(col("save_location")))

In [0]:
# Whilst performing EDA, there are several columns that contain values that are empty or contain no relevant data.
# We will now replace all these values with None:

# Replacing the "Image src error." with None in the image_src column:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("image_src", when(col("image_src") == "Image src error.", None).otherwise(col("image_src")))

# Replacing the "N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e" with None in the tag_list column:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("tag_list", when(col("tag_list") == "N,o, ,T,a,g,s, ,A,v,a,i,l,a,b,l,e", None).otherwise(col("tag_list")))

# Replacing the "No description available" & the "No description available Story format" with None from the description column:
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("description", when((col("description") == "No description available") | (col("description") == "No description available Story format"), None).otherwise(col("description")))

# Replacing the blanks, "loading..." with None in the 'title' column"
pin_T_0e1f6d6285c1_df = pin_T_0e1f6d6285c1_df.withColumn("title", when((col("title") == "") | (col("title") == "Loading..."), None).otherwise(col("title")))

### Transforming the Geolocation data:

In [0]:
# Creating a new column called "coordinates" that contains an array based on the latitute and longitude columns:
geo_T_0e1f6d6285c1_df = geo_E_0e1f6d6285c1_df.withColumn("coordinates", array(col("latitude"), col("longitude")))

In [0]:
# Dropping the latitude and longitude columns and reordering the columns:
desired_geo_columns = ["ind", "country", "coordinates", "timestamp"]

geo_T_0e1f6d6285c1_df = geo_T_0e1f6d6285c1_df.select(desired_geo_columns)

In [0]:
# Whilst performing a simple count on distinct values in the 'ind' column, results show that there are several identical rows of data, to drop these duplicates:
geo_T_0e1f6d6285c1_df = geo_T_0e1f6d6285c1_df.dropDuplicates(["ind"])

### Transforming the User data:

In [0]:
# Creating a new column 'user_name' which concatenates the information found in the 'first_name' and 'last_name' columns:
user_T_0e1f6d6285c1_df = user_E_0e1f6d6285c1_df.withColumn("user_name", concat(col("first_name"), lit(" "), col("last_name")))

In [0]:
# Dropping the first_name and last_name columns and reordering the columns:
desired_user_columns = ["ind", "user_name", "age", "date_joined"]

user_T_0e1f6d6285c1_df = user_T_0e1f6d6285c1_df.select(desired_user_columns)

In [0]:
# Whilst performing a simple count on distinct values in the 'ind' column, results show that there are several identical rows of data, to drop these duplicates:
user_T_0e1f6d6285c1_df = user_T_0e1f6d6285c1_df.dropDuplicates(["ind"])

In [0]:
# Displaying fully transformed pinterest posts dataframe:
display(pin_T_0e1f6d6285c1_df)

ind unique_id title description follower_count poster_name tag_list is_image_or_video image_src save_location category 1270 a61c8535-5585-4683-84d1-3caa5c44007f DIY All-Natural Pore-Perfecting Rose Facial Toner | Body Unburdened Many people associate roses with beauty and romance. But me? Roses make me think of my grandfather. Specifically his nose. You see, my grandfather’s honker was a bit bulbous, an…  62000 Body Unburdened | Natural Skincare | Clear Skin | Holistic Health Beauty Care,Diy Beauty,Beauty Skin,Beauty Hacks,Beauty Ideas,Face Beauty,Beauty Makeup,Natural Beauty Tips,Health And Beauty Tips image https://i.pinimg.com/originals/b3/e6/3b/b3e63b5f71349ffb8187aab278520d69.png /data/beauty beauty 2393 6c9ffdc6-d361-44af-8259-91a862ff3868 61 Stunning Christmas Tree Decorations - Chaylor & Mads The best Christmas tree decorations for every style. Some are so unique they will blow your mind! Plus, find where to get the best trees and decor this year. 91000 Kristen | Lifestyle, Mom Tips & Teacher Stuff Blog White Christmas Tree Decorations,Elegant Christmas Trees,Christmas Holidays,Christmas Wreaths,Christmas Ideas,Flocked Christmas Trees Decorated,Christmas 2019,Xmas Trees,Christmas Quotes image https://i.pinimg.com/originals/90/b5/89/90b589959a296be4c2b402bb265504b0.png /data/christmas christmas 2572 cd7502cb-8a34-4b59-b677-19ba7f4b79a4 Top 5 Moments of Hallmark’s ‘Christmas at the Plaza’ With Ryan Paevey A Christmas movie and a holiday mystery in one. Ryan Paevey played Detective Nathan West on General Hospital until his demise in 2018 and Soaps.com has been following him for th…  787000 SheKnows Christmas Party Ideas For Teens,Christmas Party Games,Christmas Activities,Christmas Traditions,Holiday Fun,Holiday Ideas,Christmas Drinking Games,Movie Drinking Games,Merry Little Christmas image https://i.pinimg.com/originals/45/58/39/455839acee56740f449b87237947cc6f.jpg /data/christmas christmas 9454 6f5c89d1-b551-47da-88b7-83dbcee5de41 Australian Shepherd Dog Tattoos Combo Outfit Legging + Hollow Tank For Women Pl - M / L Save on shipping and order more than one combo. PLEASE READ THE SIZE CHART CAREFULLY BEFORE CHOOSING YOUR SIZE. - Material: Polyester fiber (polyester), Moderate softness, cotto…  2000 Amaze Style Dachshund Shirt,Dog Hoodie,Australian Shepherd Dogs,Dog Mom Shirt,Dog Tattoos,Beautiful Dogs,Fashion Company,High Definition,Size Chart image https://i.pinimg.com/originals/1e/09/b7/1e09b747aa44759ad8d7231f34ffba4b.jpg /data/tattoos tattoos 8924 b055bda3-ca57-492b-b42e-532327fbc921 5000+ Best Tattoo Ideas | Med Tech #designtattoo #tattoo Unterarm Armbinde Tattoo-Designs Tribal-Bilder Tattoo-Samoa-Design P #Tattoo #TattooDesigns #tattoos 413 Grace Forearm Tattoos,Arm Band Tattoo,Body Art Tattoos,Tribal Tattoos,Sleeve Tattoos,Tatoos,Turtle Tattoos,Buddha Tattoos,Stomach Tattoos image https://i.pinimg.com/originals/40/01/2f/40012f47d580f121c861206d5ce5af3b.jpg /data/tattoos tattoos 5345 98b99fa5-f6b7-4a26-b95c-8e602d222a20 14 Money Tips Dave Ramsey Wish Everyone Knew Sooner In the realm of personal finance, Dave Ramsey seems to have a huge influence on people, and for good reasons. Dave Ramsey provides good advice on personal finance, financial pla…  30000 Prosmartrepreneur Best Money Saving Tips,Ways To Save Money,Money Tips,Saving Money,Money Budget,Money Hacks,Budgeting Finances,Budgeting Tips,Faire Son Budget image https://i.pinimg.com/originals/50/29/9a/50299a2b700e6071f7301a6bb2eba2ed.png /data/finance finance 6825 89cf5cc7-d755-4948-8563-60fa485e6953 This Fall's Best New Henleys There's a good reason why the casual, collarless button-up is a favorite of both Walt Whitman and Ryan Gosling. 49000 Men's Journal Mode Masculine,Masculine Style,Sharp Dressed Man,Well Dressed Men,Stylish Men,Men Casual,Casual Attire,Casual Fall,Casual Styles image https://i.pinimg.com/originals/71/f2/69/71f26954c698e73ee68ebe11d1620725.jpg /data/mens-fashion mens-fashion 1139 8c4606b6-b9fe-4f15-ac51-f0654c359a46 Make-Up-Quickie: Fen

In [0]:
# Displaying fully transformed geolocation dataframe:
display(geo_T_0e1f6d6285c1_df)

ind country coordinates timestamp 1270 Western Sahara List(-19.774, -160.69) 2018-04-02T13:53:37.000+0000 2393 Anguilla List(-89.1797, -174.015) 2021-07-26T13:12:01.000+0000 2572 Algeria List(-53.9169, -104.473) 2018-04-18T03:19:13.000+0000 9454 Azerbaijan List(-68.2139, -44.4492) 2018-02-28T22:49:47.000+0000 8924 Benin List(-86.738, -169.385) 2018-07-03T22:33:10.000+0000 5345 Congo List(-60.4924, -95.676) 2021-04-23T05:40:29.000+0000 6825 United Arab Emirates List(-44.2199, 69.4942) 2020-02-24T14:55:16.000+0000 1139 France List(-68.4636, 112.577) 2018-05-06T18:02:56.000+0000 6266 Argentina List(-89.63, -179.022) 2022-02-28T18:16:08.000+0000 7879 Algeria List(-89.5173, -179.689) 2018-09-10T05:40:21.000+0000 1884 Belarus List(-54.336, -130.459) 2018-10-29T05:21:21.000+0000 4186 Falkland Islands (Malvinas) List(-72.0557, -5.16099) 2018-09-10T12:52:21.000+0000 8743 Albania List(-88.8298, -170.188) 2021-09-21T20:54:57.000+0000 2231 Aruba List(49.9993, 146.77) 2019-02-01T11:45:52.000+0000 10768 Burkina Faso List(15.2292, 8.96859) 2018-10-03T01:08:21.000+0000 5223 Brazil List(60.6981, -79.5945) 2020-10-18T23:51:28.000+0000 7066 Germany List(18.6589, -21.2127) 2022-04-28T01:32:31.000+0000 3089 Albania List(-89.9787, -173.293) 2018-02-28T05:31:29.000+0000 9946 Greenland List(19.4001, 165.158) 2020-01-04T20:05:34.000+0000 1975 Anguilla List(-69.0778, -139.194) 2019-03-29T01:07:34.000+0000 6361 Cambodia List(15.0362, 130.283) 2018-01-11T12:06:17.000+0000 5482 Afghanistan List(-89.328, -175.555) 2020-12-12T14:09:29.000+0000 1265 Honduras List(-41.6133, 33.6532) 2021-03-07T12:27:29.000+0000 2025 American Samoa List(-88.5252, -172.436) 2021-11-08T16:23:39.000+0000 10745 Armenia List(-82.9685, -178.095) 2022-05-19T19:19:36.000+0000 2923 Cote d'Ivoire List(-84.6302, -164.507) 2019-09-08T22:53:09.000+0000 251 Isle of Man List(-66.9418, -30.0087) 2019-02-26T04:37:29.000+0000 8396 Finland List(-70.0858, 2.46314) 2020-04-18T14:17:25.000+0000 9209 Bosnia and Herzegovina List(-86.7478, -167.233) 2019-08-07T20:39:54.000+0000 4172 British Virgin Islands List(-72.8879, -131.966) 2019-01-08T12:49:09.000+0000 8011 French Polynesia List(44.8017, -151.313) 2020-07-09T22:55:35.000+0000 8172 Cayman Islands List(-67.1282, -54.1979) 2018-06-19T23:20:41.000+0000 1198 Finland List(6.37207, -150.73) 2020-01-24T23:42:18.000+0000 4321 France List(87.2391, -71.4652) 2022-01-22T17:23:44.000+0000 5367 Bulgaria List(-82.6768, -129.202) 2020-08-30T08:39:41.000+0000 10290 Ecuador List(-82.0334, -110.476) 2020-08-22T01:13:49.000+0000 7647 Algeria List(-89.5173, -179.689) 2021-06-29T06:17:19.000+0000 4132 Albania List(-89.8908, -179.887) 2020-05-05T04:43:11.000+0000 8961 Anguilla List(-75.2201, -110.456) 2022-09-11T00:33:41.000+0000 7103 Armenia List(-81.8638, 2.28085) 2021-10-06T10:15:50.000+0000 642 Afghanistan List(4.21689, -145.82) 2020-11-20T16:03:25.000+0000 1924 Anguilla List(-89.1797, -174.015) 2019-05-28T18:56:16.000+0000 2663 American Samoa List(-85.7998, -109.58) 2018-05-11T07:02:11.000+0000 4865 Iraq List(-41.9789, 90.1207) 2018-07-21T10:35:23.000+0000 4415 Micronesia List(9.71037, 56.6431) 2019-05-18T14:06:56.000+0000 4992 Aruba List(-82.0592, -92.7514) 2018-05-11T23:05:40.000+0000 6737 Afghanistan List(-88.3754, -164.273) 2017-12-10T20:29:41.000+0000 6419 Belgium List(-77.6551, -130.31) 2018-03-17T18:33:43.000+0000 1183 Gibraltar List(-76.3087, 136.595) 2018-05-24T16:45:49.000+0000 101 Albania List(-88.8298, -170.188) 2020-12-30T22:16:20.000+0000 2342 Japan List(66.9149, 113.131) 2022-03-01T05:29:16.000+0000 5597 Azerbaijan List(-32.1812, -138.244) 2021-12-26T15:04:53.000+0000 4683 Palestinian Territory List(89.5646, 179.636) 2018-12-06T18:45:09.000+0000 9957 Moldova List(12.9344, -8.73686) 2017-11-28T17:40:03.000+0000 2003 Korea List(-71.6774, 8.65135) 2018-09-16T15:45:46.000+0000 6933 Aruba List(-86.4063, -136.657) 2020-12-16T07:21:49.000+0000 8442 Antigua and Barbuda List(-88.0974, -172.052) 2021-02-23T09:59:30.000+0000 7613 Algeria List(-89.5173, -179.6

In [0]:
# Displaying fully transformed user dataframe:
display(user_T_0e1f6d6285c1_df)

ind user_name age date_joined 8258 Christopher Dixon 60 2017-05-23T01:47:05.000+0000 6790 Sean Franklin 52 2015-11-25T03:43:16.000+0000 9468 Christine Middleton 33 2016-05-31T12:01:31.000+0000 8396 Robin Miller 50 2016-04-13T01:27:55.000+0000 5016 Brooke Brown 35 2016-03-24T12:29:52.000+0000 3741 Audrey Carlson 43 2016-06-14T12:18:24.000+0000 2323 Andre Carey 28 2015-11-16T13:20:58.000+0000 6970 Joan Brewer 51 2016-10-15T10:00:11.000+0000 10257 Nicole Armstrong 57 2016-05-15T20:39:08.000+0000 8074 Kenneth Townsend 45 2016-10-12T02:46:02.000+0000 4271 Danielle Chambers 21 2015-12-08T00:29:58.000+0000 6514 Brian Johnson 20 2016-04-22T16:08:34.000+0000 3959 Crystal Green 45 2016-04-19T21:04:51.000+0000 4860 John Martinez 38 2016-01-16T00:32:12.000+0000 1809 Roberto Norman 46 2016-11-23T05:18:59.000+0000 2942 Jessica Roberts 60 2017-05-20T19:48:27.000+0000 6624 Brittany Campbell 21 2016-02-07T15:51:55.000+0000 2492 Brandon Steele 29 2017-02-08T12:28:56.000+0000 6843 Alejandra Acevedo 20 2015-11-24T21:01:23.000+0000 7406 Alvin Adams 20 2016-01-01T13:50:40.000+0000 2618 Christopher Haynes 25 2016-02-14T23:08:47.000+0000 7603 Christopher Morales 29 2016-02-21T11:56:39.000+0000 864 Andrew Hughes 46 2016-01-04T02:28:14.000+0000 6084 Alexandria Anderson 23 2015-10-31T19:20:09.000+0000 5334 Angela Montes 29 2017-02-17T13:17:55.000+0000 5334 Angela Montes 29 2017-02-17T13:17:55.000+0000 1087 Aaron Anderson 21 2015-10-23T03:43:54.000+0000 364 Jeremy Snyder 53 2016-09-21T20:59:05.000+0000 3111 Natasha Gonzalez 51 2016-05-17T07:56:53.000+0000 3135 Alex Adams 22 2016-10-22T21:06:32.000+0000 9868 Wendy George 30 2016-07-29T16:39:21.000+0000 10663 Julie Cox 23 2016-06-23T14:38:00.000+0000 8364 Aaron Anderson 21 2015-10-24T05:35:27.000+0000 1938 Kimberly Vaughn 48 2016-05-21T16:41:17.000+0000 543 David Sweeney 35 2016-12-13T23:20:57.000+0000 8389 Todd Horne 59 2016-08-20T01:10:16.000+0000 9338 Denise Adams 21 2015-11-12T06:21:36.000+0000 8540 Andrew Anderson 23 2015-11-28T11:52:37.000+0000 4935 Sophia Ramos 42 2017-01-06T11:41:02.000+0000 7613 Aaron Abbott 20 2015-10-23T16:08:41.000+0000 10537 Ernest Cook 35 2016-09-09T21:06:04.000+0000 1321 Christina Davis 49 2015-11-11T11:07:28.000+0000 5761 Leah Franco 36 2017-04-01T04:04:00.000+0000 9400 Alexander Bailey 20 2015-10-30T11:37:32.000+0000 9345 Crystal Bennett 22 2016-03-20T10:00:32.000+0000 6451 David Hunt 21 2016-11-18T14:46:36.000+0000 5363 Kevin Fisher 40 2017-10-20T10:44:26.000+0000 8998 Abigail Bates 20 2015-11-07T20:59:32.000+0000 7267 Maurice Ortiz 45 2016-10-27T07:04:47.000+0000 6934 Crystal Davis 20 2015-11-22T04:28:31.000+0000 8845 Angela Berg 20 2015-11-10T05:57:33.000+0000 3574 Dana Mckinney 25 2015-10-25T14:27:30.000+0000 8671 Christopher Carlson 32 2016-11-28T00:22:07.000+0000 7424 Anna Lee 26 2015-12-10T21:36:11.000+0000 1628 Adam Burns 20 2015-11-27T16:06:53.000+0000 8534 Christina Aguilar 23 2015-12-09T20:29:10.000+0000 8179 Aaron Alexander 21 2015-10-25T07:36:08.000+0000 5683 Adam Cole 23 2015-11-15T23:49:12.000+0000 1141 Jennifer Davis 31 2016-02-22T16:11:57.000+0000 1737 Amy Brown 21 2015-11-08T16:14:16.000+0000 4340 Charles Moore 33 2016-12-27T06:30:24.000+0000 3378 Douglas Walker 32 2017-08-28T14:02:46.000+0000 2241 Dave Davis 36 2016-01-09T10:24:37.000+0000 9253 Pamela Daniels 39 2017-08-10T12:26:13.000+0000 1681 Dennis Garcia 27 2017-01-18T22:31:57.000+0000 10120 Jacob Baird 24 2016-02-25T08:52:45.000+0000 9046 Angela Becker 22 2016-04-03T08:54:01.000+0000 5544 Christopher Doyle 59 2016-01-10T16:41:37.000+0000 7038 Michael Rivas 53 2016-01-12T19:46:30.000+0000 4210 Anthony Golden 56 2017-05-03T22:37:43.000+0000 3774 Jacqueline Ross 49 2015-12-10T11:03:45.000+0000 3762 Kristi Foster 33 2017-09-14T23:41:12.000+0000 1555 Alexis Bennett 54 2016-05-15T04:22:01.000+0000 476 Timothy Smith 49 2016-03-01T18:50:01.000+0000 9231 Andrea Alexander 21 2015-11-10T09:27:42.000+0000 8253 Aaron Anderson 21 2015-10-24T05:35:27.000+0000 2391 Kathryn Ross 34 2016-04-17T23:11:13.000+0000 8867

## Loading the streaming data to Delta tables in Databricks

The transformations for each of the 3 streams are now complete, now we need to store them in Databricks. We will load them into Databricks by writing each of the tables to Datrabricks Delta tables.

In [0]:
# Writing the Pinterest posts dataframe to a delta table.
# We will provide and option in the query so that we can recover the previous state of a query in case of failure (data will be safe).
pin_T_0e1f6d6285c1_df.writeStream \
  .format("delta") \
  .outputMode("append") \
  .option("checkpointLocation", "/tmp/kinesis/_checkpoints_pin/") \
  .table("0e1f6d6285c1_pin_table")

Out[81]: <pyspark.sql.streaming.StreamingQuery at 0x7f2121311bb0>

In [0]:
# Writing the geolocation dataframe to a delta table.
# We will provide and option in the query so that we can recover the previous state of a query in case of failure (data will be safe).
geo_T_0e1f6d6285c1_df.writeStream \
  .format("delta") \
  .outputMode("append") \
  .option("checkpointLocation", "/tmp/kinesis/_checkpoints_geo/") \
  .table("0e1f6d6285c1_geo_table")

Out[82]: <pyspark.sql.streaming.StreamingQuery at 0x7f2114971520>

In [0]:
# Writing the user dataframe to a delta table.
# We will provide and option in the query so that we can recover the previous state of a query in case of failure (data will be safe).
user_T_0e1f6d6285c1_df.writeStream \
  .format("delta") \
  .outputMode("append") \
  .option("checkpointLocation", "/tmp/kinesis/_checkpoints_user/") \
  .table("0e1f6d6285c1_user_table")

Out[83]: <pyspark.sql.streaming.StreamingQuery at 0x7f212134ca90>

In [0]:
# In order to run the 'writeStream' function again, need to delete the checkpoint folder for each of the 3 dataframes unless the checkpoint destination is changed. If we do change it, we can gradually track the different checkpoints if necessary:
# Removing Pinterest posts checkpoint folder:
dbutils.fs.rm("/tmp/kinesis/_checkpoints_pin/", True)

# Removing geolocation checkpoint folder:
dbutils.fs.rm("/tmp/kinesis/_checkpoints_geo/", True)

# Removing user checkpoint folder:
dbutils.fs.rm("/tmp/kinesis/_checkpoints_user/", True)